In [1]:
#quickstart
from pathlib import Path
import pandas as pd
from bids import BIDSLayout
from joblib import Parallel, delayed
import nilearn
import nibabel as nib
import nltools.prefs as prf
from nilearn import datasets, image, plotting, input_data
from nilearn.masking import apply_mask
from nilearn.image import resample_to_img
from nilearn.image import concat_imgs, index_img
import numpy as np
import matplotlib.pylab as plt

import rpy2
from rpy2.robjects.packages import importr
from pymer4 import Lmer
psych = importr('psych')


import rpy2.robjects as ro
from rpy2.robjects import pandas2ri

from rpy2.robjects.conversion import localconverter

import os
import glob
import seaborn as sns
from nltools.data import Brain_Data, Design_Matrix, Adjacency
from nltools.mask import expand_mask, roi_to_brain
from nltools.stats import zscore
from scipy.stats import binom, ttest_1samp
from sklearn.metrics import pairwise_distances
from nltools.stats import fdr, one_sample_permutation
from copy import deepcopy
from nltools.utils import get_anatomical
import nltools.plotting as nlplt
from datetime import date
from joblib import Parallel, delayed

from sklearn.linear_model import LinearRegression
from sklearn.decomposition import PCA

from nilearn.input_data import NiftiMapsMasker
from nilearn.connectome import ConnectivityMeasure

#dat_paths = pd.read_csv('/data/MBDU/midla/notebooks/campcc/dat_paths_11272019.csv') 
#atlas = image.load_img('/data/MBDU/midla/notebooks/campcc/hox_msdl_atlas.nii.gz')
#sub1 = image.load_img('/data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm/sub-20900/out/fmrip

%matplotlib inline
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_colwidth', 500)
pd.set_option('display.width', 1000)

from IPython.core.display import display, HTML
display(HTML("<style>"
    + "#notebook { padding-top:0px !important; } " 
    + ".container { width:100% !important; } "
    + ".end_space { min-height:0px !important; } "
    + "</style>"))

/gpfs/gsfs11/users/MBDU/midla/env/lib/python3.7/site-packages/sklearn/externals/joblib/__init__.py:15: DeprecationWarning: sklearn.externals.joblib is deprecated in 0.21 and will be removed in 0.23. Please import this functionality directly from joblib, which can be installed with: pip install joblib. If this warning is raised when loading pickled models, you may need to re-serialize those models with scikit-learn 0.21+.
  warnings.warn(msg, category=DeprecationWarning)


In [144]:
dat_paths = pd.read_csv('/data/MBDU/midla/notebooks/campcc/dat_paths_12092019.csv')

In [37]:
for _,row in dat_paths.iterrows():
    if (os.path.isfile('/data/MBDU/midla/data/bids/sub-{}/ses-0{}/func/sub-{}_ses-0{}_task-mid_run-{}_physio.tsv.gz'.format(row.subject,row.session,row.subject,row.session,row.run))):
        phys_path = '/data/MBDU/midla/data/bids/sub-{}/ses-0{}/func/sub-{}_ses-0{}_task-mid_run-{}_physio.tsv.gz'.format(row.subject,row.session,row.subject,row.session,row.run)
        output_path = '/data/MBDU/midla/notebooks/campcc/physio/physio_subject_{}_session_{}_run_{}_task_mid'.format(row.subject,row.session,row.run)
        !/data/MBDU/midla/notebooks/campcc/afni/src/jzosky/RetroTS.py -phys_file $phys_path -p 50 -n 1 -v 2 -slice_order "Custom" -slice_offset [1000] -prefix $output_path

pause
stop
[6.0000e-02 2.4000e+00 5.0400e+00 7.9000e+00 1.0700e+01 1.3440e+01
 1.6520e+01 1.9200e+01 2.1800e+01 2.4520e+01 2.7620e+01 3.1040e+01
 3.3740e+01 3.6440e+01 3.9840e+01 4.3340e+01 4.6580e+01 4.9800e+01
 5.3300e+01 5.6380e+01 5.9460e+01 6.3240e+01 6.6060e+01 6.8980e+01
 7.2700e+01 7.5900e+01 7.8960e+01 8.2040e+01 8.5000e+01 8.8360e+01
 9.2380e+01 9.5480e+01 9.8020e+01 1.0150e+02 1.0500e+02 1.0832e+02
 1.1172e+02 1.1542e+02 1.1826e+02 1.2116e+02 1.2436e+02 1.2752e+02
 1.3006e+02 1.3296e+02 1.3628e+02 1.3942e+02 1.4254e+02 1.4512e+02
 1.4862e+02 1.5164e+02 1.5442e+02 1.5764e+02 1.6054e+02 1.6376e+02
 1.6688e+02 1.6986e+02 1.7322e+02 1.7642e+02 1.8024e+02 1.8316e+02
 1.8614e+02 1.8918e+02 1.9234e+02 1.9434e+02 1.9736e+02 2.0062e+02
 2.0382e+02 2.0712e+02 2.1026e+02 2.1336e+02 2.1640e+02 2.1930e+02
 2.2232e+02 2.2554e+02 2.2884e+02 2.3182e+02 2.3512e+02 2.3850e+02
 2.4250e+02 2.4752e+02 2.5054e+02 2.5368e+02 2.5630e+02 2.5948e+02
 2.6258e+02 2.6578e+02 2.6894e+02 2.7186e+02 2.7466

Estimating phase for respiration_info
Estimating phase for cardiac_info
[ 424.62677596  387.62677596  352.62677596 ... -488.37322404 -469.37322404
 -449.37322404]
Computing RVT from peaks
[13.6929133  13.6929133  13.6929133  ...  8.12550229  8.12550229
  8.12550229]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]
pause
stop
[1.2000e-01 4.9800e+00 7.5000e+00 9.9800e+00 1.2520e+01 1.5440e+01
 1.7820e+01 2.0400e+01 2.3100e+01 2.5580e+01 2.7880e+01 3.0480e+01
 3.3160e+01 3.5460e+01 4.0120e+01 4.3140e+01 4.5680e+01 4.8440e+01
 5.1040e+01 5.3360e+01 5.5780e+01 5.8280e+01 6.0860e+01 6.3200e+01
 6.5700e+01 6.8100e+01 7.0640e+01 7.3180e+01 7.7740e+01 8.0380e+01
 8.2840e+01 8.5420e+01 8.7820e+01 9.0480e+01 9.3000e+01 9.5560e+01
 9.8040e+01 1.0048e+02 1.0284e+02 1.0538e+02 1.0774e+02 1.1046e+02
 1.1188e+02 1.1436e+02 1.1706e+02 1.1964e+0

Estimating phase for cardiac_info
[ 821.54956284  817.54956284  811.54956284 ... -147.45043716 -115.45043716
  -83.45043716]
Computing RVT from peaks
[161.14458491 161.14458491 219.00704391 ... 881.16070014 881.16070014
 881.16070014]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]
pause
stop
[  1.18   5.96   9.82  13.14  16.66  19.26  21.62  24.88  27.72  30.5
  33.62  36.46  39.56  42.78  45.1   47.88  50.48  53.56  56.02  58.88
  62.08  64.42  67.46  70.62  73.1   75.92  78.62  81.62  84.48  87.68
  90.94  93.52  96.36  99.28 102.1  105.08 108.4  111.4  114.42 117.46
 120.74 123.7  126.7  129.92 133.44 136.48 139.64 142.38 145.2  148.64
 151.54 154.16 157.44 160.52 163.46 166.86 169.88 172.7  176.08 178.7
 181.44 185.1  187.54 190.36 193.1  195.68 198.6  201.46 204.28 207.02
 210.1  213.2  215.8  218.52 222.1  225.06 227.56

Estimating phase for respiration_info
Estimating phase for cardiac_info
[-1025.3989071 -1027.3989071 -1028.3989071 ...   213.6010929   210.6010929
   206.6010929]
Computing RVT from peaks
[ 7.04105163  7.04105163  7.04105163 ... 30.15153595 30.15153595
 30.15153595]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]
pause
stop
[  0.78   2.74   4.82   6.98   9.02  11.32  13.32  15.7   17.82  20.38
  22.34  24.62  26.78  28.78  30.88  33.2   35.18  37.22  39.36  41.54
  43.98  46.12  48.54  50.98  53.3   55.48  57.6   59.76  62.04  64.5
  66.54  68.7   71.52  73.82  77.66  80.5   82.68  84.94  86.    88.02
  90.24  92.4   94.52  96.68  99.24 101.58 103.8  106.   108.44 110.84
 113.04 115.36 117.3  119.74 122.42 125.08 127.24 129.48 131.4  133.88
 136.14 138.66 140.88 143.38 145.42 147.82 149.88 152.06 154.12 156.46
 158.02 160.36 1

Estimating phase for cardiac_info
[-164.46008197 -132.46008197 -101.46008197 ... -442.46008197 -419.46008197
 -397.46008197]
Computing RVT from peaks
[97.21042927 97.21042927 97.21042927 ...  2.0712618   2.0712618
  2.0712618 ]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]
pause
stop
[2.0000e-02 2.2400e+00 4.6600e+00 7.0400e+00 9.4800e+00 1.2000e+01
 1.4360e+01 1.6460e+01 1.8560e+01 2.1020e+01 2.3300e+01 2.5700e+01
 2.7700e+01 2.9920e+01 3.2420e+01 3.4820e+01 3.9360e+01 4.1740e+01
 4.4000e+01 4.6100e+01 4.8500e+01 5.0940e+01 5.3320e+01 5.5860e+01
 5.8320e+01 6.0620e+01 6.3080e+01 6.5240e+01 6.7640e+01 6.9920e+01
 7.2100e+01 7.4300e+01 7.7040e+01 7.8980e+01 8.1420e+01 8.3600e+01
 8.6340e+01 8.8420e+01 9.1040e+01 9.3540e+01 9.6420e+01 9.8500e+01
 1.0086e+02 1.0318e+02 1.0594e+02 1.0824e+02 1.1054e+02 1.1276e+02
 1.1546e+02 1.1

...

Estimating phase for cardiac_info
[ 288.53243169  324.53243169  360.53243169 ... -183.46756831 -161.46756831
 -138.46756831]
Computing RVT from peaks
[137.63400129 137.63400129 151.9830682  ...   7.43679719   7.43679719
   7.43679719]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]
pause
stop
[  3.42   7.52  11.32  14.7   17.96  20.86  23.92  26.4   29.52  33.04
  35.52  38.96  42.76  45.62  49.7   52.8   56.6   59.98  63.48  66.98
  70.04  72.58  75.78  79.22  81.96  85.56  88.94  91.58  94.98  98.38
 101.2  104.4  107.14 110.04 112.76 115.72 118.58 121.14 124.36 127.76
 130.5  134.58 137.8  141.08 144.8  147.64 149.66 152.98 156.34 160.76
 164.44 166.76 170.2  174.04 177.08 180.06 182.6  185.28 188.22 191.7
 194.28 196.76 199.44 202.3  205.16 208.38 211.48 214.16 217.52 220.3
 222.58 225.44 228.36 231.3  234.48 237.48 240.9 

Estimating phase for respiration_info
Estimating phase for cardiac_info
[-208.98409836 -193.98409836 -177.98409836 ... -136.98409836 -116.98409836
  -97.98409836]
Computing RVT from peaks
[123.09461463 123.09461463 136.79767691 ...  14.34444645  14.34444645
  14.34444645]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]
pause
stop
[  1.78   4.2    6.6    9.22  11.76  14.14  16.4   18.7   21.06  23.32
  25.58  27.6   29.92  32.18  34.54  36.74  38.92  41.22  43.64  46.22
  48.76  51.1   53.44  56.04  58.58  61.    63.18  65.44  67.74  70.12
  72.2   74.4   76.76  79.28  81.72  84.22  86.8   89.36  91.76  93.98
  96.6   99.1  101.48 104.14 106.46 108.8  111.3  113.44 115.76 118.12
 120.38 122.72 124.7  126.96 130.16 132.94 135.   137.56 139.78 142.24
 144.44 146.92 149.   151.52 153.52 156.16 158.56 161.26 163.32 165.64
 168.38 1

pause
stop
[6.0000e-02 9.8000e-01 2.1000e+00 2.9200e+00 3.6400e+00 4.4200e+00
 5.2400e+00 5.5600e+00 6.3600e+00 7.5000e+00 8.5200e+00 9.4000e+00
 1.0320e+01 1.1460e+01 1.2600e+01 1.3660e+01 1.4680e+01 1.5600e+01
 1.6540e+01 1.7480e+01 1.8380e+01 1.9260e+01 2.0100e+01 2.1020e+01
 2.1900e+01 2.2740e+01 2.3640e+01 2.4740e+01 2.5560e+01 2.6420e+01
 2.7400e+01 2.8240e+01 2.9080e+01 2.9960e+01 3.0820e+01 3.1700e+01
 3.2820e+01 3.3740e+01 3.4600e+01 3.5760e+01 3.6760e+01 3.7660e+01
 3.8520e+01 3.9340e+01 4.0200e+01 4.1340e+01 4.2360e+01 4.3200e+01
 4.4080e+01 4.4880e+01 4.5780e+01 4.6860e+01 4.7740e+01 4.8680e+01
 4.9680e+01 5.0560e+01 5.1580e+01 5.2460e+01 5.3280e+01 5.4260e+01
 5.5300e+01 5.6200e+01 5.7240e+01 5.8100e+01 5.8920e+01 5.9840e+01
 6.0860e+01 6.1800e+01 6.2640e+01 6.3480e+01 6.4280e+01 6.5060e+01
 6.5800e+01 6.6540e+01 6.7300e+01 6.8460e+01 6.9520e+01 7.0580e+01
 7.1420e+01 7.2200e+01 7.3020e+01 7.3880e+01 7.4840e+01 7.5800e+01
 7.6760e+01 7.7780e+01 7.8640e+01 7.9580e+01 8.0560

Estimating phase for cardiac_info
[2497.47770492 2497.47770492 2497.47770492 ... -408.52229508 -408.52229508
 -408.52229508]
Computing RVT from peaks
[278.21877234 278.21877234 278.21877234 ... 154.45853274 154.45853274
 154.45853274]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]
pause
stop
[  1.06   3.16   5.46   7.74  10.1   12.78  15.46  17.9   20.02  23.46
  25.9   28.54  30.82  33.26  35.68  38.38  41.22  44.34  46.9   49.12
  51.58  54.    56.54  59.22  61.74  64.54  68.52  71.1   73.6   76.48
  79.22  81.92  84.24  86.82  89.5   91.88  94.36  96.94 100.02 102.4
 104.76 107.16 110.08 112.64 115.26 117.72 119.84 122.26 124.94 127.32
 129.74 132.08 134.6  136.82 138.86 140.84 144.18 146.48 148.96 151.68
 154.24 156.66 159.2  161.92 164.28 166.82 169.28 171.78 174.54 177.04
 179.7  183.06 185.64 188.02 190.5  193.78 196.7

Estimating phase for respiration_info
Estimating phase for cardiac_info
[1237.52696721 1272.52696721 1315.52696721 ... -561.47303279 -558.47303279
 -554.47303279]
Computing RVT from peaks
[17.46490606 17.46490606 17.46490606 ... 55.84322248 55.84322248
 55.84322248]
[    0     1     2 ... 36597 36598 36599]
[  250   251   252 ... 36847 36848 36849]
[  500   501   502 ... 37097 37098 37099]
[  750   751   752 ... 37347 37348 37349]
[ 1000  1001  1002 ... 37597 37598 37599]


In [205]:
rest_paths = pd.read_csv('/data/MBDU/midla/notebooks/campcc/dat_paths_rest.csv')

included_subjects = pd.read_csv('/data/MBDU/midla/notebooks/campcc/test_retest/included_subjects.csv',index_col = 0)
rest_paths = rest_paths[rest_paths['subject'].isin(included_subjects['SDAN'])]
rest_paths = rest_paths.loc[rest_paths[rest_paths.columns[5:7]].duplicated(keep='last') == False]

single_ses_subs = rest_paths.loc[rest_paths.session.astype(int) <= 4, :].groupby('subject').session.nunique().reset_index().query('session <= 2').subject
rest_ind = ~rest_paths.subject.isin(single_ses_subs) & (rest_paths.session.astype(int) <= 4)
rest_paths = rest_paths.loc[rest_ind]

rest_paths.reset_index(inplace=True)
rest_paths = rest_paths.drop(columns=['index'])

In [206]:
for _,row in rest_paths.iterrows():
    if (os.path.isfile('/data/MBDU/midla/data/bids/sub-{}/ses-0{}/func/sub-{}_ses-0{}_task-rest_run-{}_physio.tsv.gz'.format(row.subject,row.session,row.subject,row.session,row.run))):
        phys_path = '/data/MBDU/midla/data/bids/sub-{}/ses-0{}/func/sub-{}_ses-0{}_task-rest_run-{}_physio.tsv.gz'.format(row.subject,row.session,row.subject,row.session,row.run)
        output_path = '/data/MBDU/midla/notebooks/campcc/physio/rest/physio_subject_{}_session_{}_run_{}_task_rest'.format(row.subject,row.session,row.run)
        !/data/MBDU/midla/notebooks/campcc/afni/src/jzosky/RetroTS.py -phys_file $phys_path -p 50 -n 1 -v 2.5 -slice_order "Custom" -slice_offset [1250] -prefix $output_path

pause
stop
[  1.44   3.52   5.66   7.86  10.42  12.88  15.52  18.14  20.38  22.7
  25.12  27.8   30.22  32.8   35.22  37.68  39.88  42.04  44.5   46.84
  49.28  51.56  53.82  56.26  58.74  61.04  63.26  65.68  68.1   70.6
  73.44  76.16  79.    81.54  84.1   86.4   89.04  91.68  94.14  96.6
  99.02 101.3  103.56 105.9  108.44 110.66 112.96 115.72 118.26 120.66
 123.04 125.66 128.18 130.66 133.22 135.72 138.16 140.56 143.02 145.68
 148.   150.48 153.12 155.5  157.96 160.16 162.6  165.14 167.6  170.06
 172.8  175.16 177.38 180.02 182.58 185.12 187.56 190.04 192.3  194.66
 196.96 199.74 202.36 205.   207.34 209.7  214.14 216.52 219.12 221.56
 223.78 226.26 228.56 231.24 233.6  236.04 238.68 241.12 243.48 245.42
 247.76 250.36 252.6  255.06 257.46 260.14 262.72 265.46 268.38 270.64
 273.24 275.68 277.9  280.44 283.   285.12 287.9  290.16 292.56 294.68
 297.16 299.76 302.54 305.18 307.74 311.08 314.26 317.92 321.02 323.
 324.78 327.86 332.12 334.5  336.8  339.44 342.18 344.64 346.48 348.68


Estimating phase for respiration_info
Estimating phase for cardiac_info
[-238.95693878 -246.95693878 -253.95693878 ... -212.95693878 -189.95693878
 -168.95693878]
Computing RVT from peaks
[733.2806001  733.2806001  733.2806001  ... 179.26704219 179.26704219
 179.26704219]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]
pause
stop
[  1.82   4.18   6.7   11.32  14.28  15.54  17.86  20.84  23.7   26.14
  28.92  31.72  34.26  36.98  39.32  41.    43.56  46.72  49.6   52.08
  54.52  56.92  59.5   62.16  64.7   67.14  70.12  72.64  75.06  77.72
  80.12  82.68  85.26  87.9   90.64  93.22  95.9   98.42 101.04 103.48
 106.08 108.56 111.16 113.42 118.18 120.92 123.06 125.42 128.14 130.68
 133.2  136.   138.22 140.68 142.94 145.66 147.88 150.38 153.12 155.66
 158.3  160.88 171.78 179.54 182.76 185.52 188.12 190.58 193.08 195.8
 198.18 20

Estimating phase for respiration_info
Estimating phase for cardiac_info
[-103.28163265 -116.28163265 -131.28163265 ... -157.28163265 -163.28163265
 -169.28163265]
Computing RVT from peaks
[498.41705861 498.41705861 498.41705861 ... -75.72497633 -75.72497633
 -75.72497633]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]
pause
stop
[  1.72   7.36  10.62  14.34  17.46  19.96  24.4   27.48  31.22  35.44
  38.64  42.68  45.9   49.66  52.56  56.16  59.08  65.82  68.9   71.96
  75.3   79.02  81.7   84.78  90.7   93.42  95.84  98.44 101.2  104.42
 107.26 110.16 112.84 115.98 118.92 121.62 124.72 127.6  130.92 133.72
 137.   140.02 142.72 145.86 149.02 153.2  164.94 172.68 180.54 183.5
 185.94 191.02 196.54 212.42 215.2  218.54 221.28 230.48 232.6  235.1
 237.9  241.54 244.16 246.76 249.42 252.34 256.   259.76 262.56 265.74
 268.34 270

Estimating phase for cardiac_info
[-178.32881633 -156.32881633 -134.32881633 ... -434.32881633 -425.32881633
 -413.32881633]
Computing RVT from peaks
[2545.77884933 2545.77884933 2545.77884933 ... 1961.41747537 1961.41747537
 1961.41747537]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]
pause
[  4.56  10.46  14.36  17.78  22.7   26.84  32.24  35.8   39.96  43.42
  48.56  52.84  56.9   60.86  65.26  69.54  73.46  77.84  81.3   85.58
  89.44  92.52  96.54 100.18 104.08 107.9  112.08 116.4  125.32 131.56
 142.22 149.44 154.66 158.94 162.7  165.9  169.54 173.04 176.76 182.54
 197.32 201.08 205.48 209.24 213.34 216.9  220.42 226.46 231.32 237.
 242.06 246.06 250.38 255.12 259.1  262.58 267.24 272.02 275.82 280.02
 283.32 287.42 290.64 294.56 300.1  304.26 308.78 315.9  319.54 323.92
 327.22 331.08 334.54 337.42 347.86 351.72 356.1

Estimating phase for cardiac_info
[-194.52857143 -203.52857143 -212.52857143 ...  823.47142857  833.47142857
  845.47142857]
Computing RVT from peaks
[663.32267961 663.32267961 663.32267961 ... 477.27687548 477.27687548
 477.27687548]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]
pause
stop
[  1.62   7.54  10.74  15.16  18.82  22.58  26.56  31.14  37.16  42.62
  46.76  50.66  53.74  56.56  59.46  62.46  65.76  68.78  71.94  74.68
  78.16  81.46  85.34  88.76  92.2   95.58  98.78 102.2  105.32 109.14
 112.8  115.98 119.1  122.2  125.22 128.2  131.3  134.42 137.84 140.5
 143.82 147.08 150.34 153.62 156.9  159.96 163.02 166.26 169.48 172.84
 176.44 180.4  184.36 188.3  191.7  194.54 197.34 200.02 203.1  207.56
 212.46 221.1  225.26 229.12 232.82 236.22 239.52 242.66 245.62 248.8
 252.36 256.46 260.26 264.26 266.56 270.8  275.84

...

pause
stop
[  0.6    1.42   2.28   3.04   3.78   4.58   5.36   6.14   6.94   7.78
   8.62   9.38  10.2   11.04  11.9   12.44  13.4   14.1   14.8   15.56
  16.36  17.12  17.88  18.62  19.42  20.22  20.94  21.7   22.46  23.32
  24.08  24.8   25.54  26.32  27.04  27.76  28.5   29.34  30.06  30.78
  31.48  32.22  32.58  33.08  33.78  34.5   35.2   35.9   36.66  37.42
  38.24  39.04  39.88  40.62  41.38  42.1   42.78  43.48  44.22  45.06
  45.84  46.64  47.42  48.04  48.8   49.56  50.36  51.16  51.9   52.68
  53.44  54.22  54.94  55.7   56.48  57.24  58.06  58.88  59.62  60.36
  61.14  61.92  62.72  63.52  64.28  65.02  65.82  66.58  67.38  68.14
  68.92  69.7   70.5   71.24  71.98  72.72  73.52  74.24  75.    75.64
  76.4   77.2   78.02  78.38  78.86  79.6   80.32  81.08  81.88  82.72
  83.52  84.32  85.1   85.92  86.74  87.5   88.26  89.02  89.82  90.64
  91.44  92.24  92.98  93.76  94.58  95.3   96.06  96.82  97.6   98.38
  99.1   99.86 100.6  101.28 101.98 103.4  104.04 104.68 105.36 10

Estimating phase for cardiac_info
[ 665.19620408  629.19620408  591.19620408 ... -522.80379592 -524.80379592
 -529.80379592]
Computing RVT from peaks
[423.73235045 423.73235045 423.73235045 ... 127.28157428 127.28157428
 127.28157428]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]
pause
[1.2000e-01 3.9600e+00 9.8000e+00 1.2660e+01 1.5720e+01 1.9460e+01
 2.4860e+01 2.9400e+01 3.5200e+01 4.0300e+01 4.6520e+01 5.0180e+01
 5.5780e+01 6.0080e+01 6.4100e+01 6.8160e+01 7.2380e+01 7.8460e+01
 8.0800e+01 8.3880e+01 8.7280e+01 9.5040e+01 9.8900e+01 1.0972e+02
 1.1408e+02 1.2176e+02 1.2978e+02 1.3358e+02 1.3886e+02 1.4620e+02
 1.5226e+02 1.5988e+02 1.6414e+02 1.7086e+02 1.7682e+02 1.8032e+02
 1.8558e+02 1.9198e+02 1.9538e+02 2.0058e+02 2.0334e+02 2.0562e+02
 2.1072e+02 2.1428e+02 2.1808e+02 2.2592e+02 2.3006e+02 2.3224e+02
 2.4198e+02 2

Estimating phase for cardiac_info
[-143.666 -118.666  -86.666 ...  295.334  280.334  264.334]
Computing RVT from peaks
[300.78341715 300.78341715 294.11540858 ... 120.18544003 120.18544003
 120.18544003]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]
pause
stop
[  4.44   8.28  11.02  14.82  19.12  22.32  25.98  29.4   31.94  34.86
  39.14  43.98  47.52  51.1   53.46  55.9   58.6   61.38  69.96  72.12
  76.08  78.74  81.64  84.14  87.88  92.84  98.94 102.74 105.96 108.54
 117.16 120.78 124.1  128.04 130.36 133.36 136.12 140.5  142.66 145.2
 149.   152.52 154.6  157.64 159.94 165.48 170.22 172.18 174.44 176.8
 179.5  190.1  197.72 199.74 202.28 209.12 212.6  216.6  219.02 226.4
 229.22 231.16 233.62 236.84 240.54 243.04 246.68 248.86 252.92 255.28
 258.56 270.   277.56 281.58 284.3  286.5  288.96 296.08 297.86 300.06
 302.34 30

Estimating phase for cardiac_info
[  20.25465306   49.25465306   77.25465306 ... -120.74534694 -103.74534694
  -86.74534694]
Computing RVT from peaks
[370.6047631  370.6047631  370.6047631  ... 128.97484037 128.97484037
 128.97484037]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]
pause
[  1.48   4.3   14.2   17.92  23.18  27.82  31.2   34.7   39.46  44.64
  49.22  52.92  56.48  61.48  66.58  70.26  75.14  79.18  82.74  86.88
 100.5  109.12 120.48 123.22 125.98 128.82 132.4  136.16 141.6  146.92
 151.7  163.44 167.86 171.86 175.78 180.56 185.28 188.24 193.12 197.68
 201.18 205.08 208.54 212.06 215.2  220.46 224.54 227.84 232.08 236.46
 241.42 247.24 250.92 254.66 257.66 260.54 264.06 269.9  281.76 289.36
 297.6  302.04 305.84 311.06 313.94 318.52 324.64 328.68 331.96 336.1
 341.04 344.1  348.82 353.1  358.78 362.8  368.46 372

Estimating phase for respiration_info
Estimating phase for cardiac_info
[-336.70571429 -350.70571429 -364.70571429 ... -445.70571429 -444.70571429
 -443.70571429]
Computing RVT from peaks
[2.15077800e+02 2.15077800e+02 2.15077800e+02 ... 1.56246132e-01
 1.56246132e-01 1.56246132e-01]
[    0     1     2 ... 24497 24498 24499]
[  250   251   252 ... 24747 24748 24749]
[  500   501   502 ... 24997 24998 24999]
[  750   751   752 ... 25247 25248 25249]
[ 1000  1001  1002 ... 25497 25498 25499]


In [119]:
for _,row in dat_paths.iterrows():
    if os.path.isfile('/data/MBDU/midla/notebooks/campcc/physio/mid/physio_subject_{}_session_{}_run_{}_task_mid.slibase.1D'.format(row.subject,row.session,row.run)):
        file = pd.read_csv('/data/MBDU/midla/notebooks/campcc/physio/mid/physio_subject_{}_session_{}_run_{}_task_mid.slibase.1D'.format(row.subject,row.session,row.run))
        df = pd.DataFrame()
        for i in range(len(file)):
            if i in [0,1]:
                continue
            elif i == 3:
                continue
            elif i == 2:
                line = file.iloc[i][0].split(' ; ')
                for j in range(len(line)):
                    if j == 0:
                        df['s0.RVT0'] = 0.0
                    elif j == len(line)-1:
                        df['s0.Card3'] = 0.0
                    else:
                        df[line[j]] = 0.0
            elif i == len(file)-1:
                continue
            else:
                line = file.iloc[i][0].split(' ')
                X = []
                for j in range(len(line)):
                    X.append(float(line[j]))
                df.loc[i-4] = X
        df.to_csv('/data/MBDU/midla/notebooks/campcc/physio/mid_df/physio_subject_{}_session_{}_run_{}_task_mid'.format(row.subject,row.session,row.run))

In [207]:
for _,row in rest_paths.iterrows():
    if os.path.isfile('/data/MBDU/midla/notebooks/campcc/physio/rest/physio_subject_{}_session_{}_run_{}_task_rest.slibase.1D'.format(row.subject,row.session,row.run)):
        file = pd.read_csv('/data/MBDU/midla/notebooks/campcc/physio/rest/physio_subject_{}_session_{}_run_{}_task_rest.slibase.1D'.format(row.subject,row.session,row.run))
        df = pd.DataFrame()
        for i in range(len(file)):
            if i in [0,1]:
                continue
            elif i == 3:
                continue
            elif i == 2:
                line = file.iloc[i][0].split(' ; ')
                for j in range(len(line)):
                    if j == 0:
                        df['s0.RVT0'] = 0.0
                    elif j == len(line)-1:
                        df['s0.Card3'] = 0.0
                    else:
                        df[line[j]] = 0.0
            elif i == len(file)-1:
                continue
            else:
                line = file.iloc[i][0].split(' ')
                X = []
                for j in range(len(line)):
                    X.append(float(line[j]))
                df.loc[i-4] = X
        df.to_csv('/data/MBDU/midla/notebooks/campcc/physio/rest_df/physio_subject_{}_session_{}_run_{}_task_rest.csv'.format(row.subject,row.session,row.run))

In [217]:
for _,row in rest_paths.iterrows():
    cfds = pd.read_csv(row.confounds_path, sep='\t')
    try:
        physio = pd.read_csv('/data/MBDU/midla/notebooks/campcc/physio/rest_df/physio_subject_{}_session_{}_run_{}_task_rest.csv'.format(row.subject,row.session,row.run),index_col=0)
        cfds = pd.concat([cfds,physio],axis=1,sort=False)
        cfds.to_csv('/data/MBDU/midla/notebooks/campcc/physio/new_cfds_rest/new_cfds_rest_subject_{}_session_{}_run_{}_task_rest.tsv'.format(row.subject,row.session,row.run),sep='\t')
    except FileNotFoundError:
        continue

In [122]:
for _,row in dat_paths.iterrows():
    cfds = pd.read_csv(row.confounds_path, sep='\t')
    try:
        physio = pd.read_csv('/data/MBDU/midla/notebooks/campcc/physio/mid_df/physio_subject_{}_session_{}_run_{}_task_mid'.format(row.subject,row.session,row.run),index_col=0)
        cfds = pd.concat([cfds,physio],axis=1,sort=False)
        cfds.to_csv('/data/MBDU/midla/notebooks/campcc/physio/new_cfds_mid/new_cfds_mid_subject_{}_session_{}_run_{}_task_mid.tsv'.format(row.subject,row.session,row.run),sep='\t')
    except FileNotFoundError:
        continue

In [218]:
cfds_physio = []
for _,row in rest_paths.iterrows():
    if (os.path.isfile('/data/MBDU/midla/data/bids/sub-{}/ses-0{}/func/sub-{}_ses-0{}_task-rest_run-{}_physio.tsv.gz'.format(row.subject,row.session,row.subject,row.session,row.run))):
        cfds_physio.append('/data/MBDU/midla/notebooks/campcc/physio/new_cfds_rest/new_cfds_rest_subject_{}_session_{}_run_{}_task_rest.tsv'.format(row.subject,row.session,row.run))
    else:
        cfds_physio.append('')
rest_paths['cfds_physio_path'] = cfds_physio


In [211]:
rest_paths

confounds_path                                                                                                                                                                                                     image_path                                                                                                                                                                mask_path  run                                                                                                                                                                                                  scaled_path  session  subject  task                                                                                                  cfds_physio_path
0    /data/MBDU/midla/data/derivatives/fitlins/rest_dm_only/sub-21748/ses-01/run-1/out/out/fitlins/sub-21748/ses-01/sub-21748_ses-01_task-rest_run-1_design.tsv  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/ses-01/func/sub-21748_ses-01_task-rest_run-1_echo-2_space-MNI152NLin2009cAsym_desc-preproc_bold.nii.gz  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/anat/sub-21748_space-MNI152NLin2009cAsym_label-GM_probseg.nii.gz    1  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/ses-01/func/sub-21748_ses-01_task-rest_run-1_echo-2_space-MNI152NLin2009cAsym_desc-scale_bold.nii.gz        1    21748  rest  /data/MBDU/midla/notebooks/campcc/physio/new_cfds_rest/new_cfds_rest_subject_21748_session_1_run_1_task_rest.tsv
1    /data/MBDU/midla/data/derivatives/fitlins/rest_dm_only/sub-21748/ses-02/run-1/out/out/fitlins/sub-21748/ses-02/sub-21748_ses-02_task-rest_run-1_design.tsv  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/ses-02/func/sub-21748_ses-02_task-rest_run-1_echo-2_space-MNI152NLin2009cAsym_desc-preproc_bold.nii.gz  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/anat/sub-21748_space-MNI152NLin2009cAsym_label-GM_probseg.nii.gz    1  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/ses-02/func/sub-21748_ses-02_task-rest_run-1_echo-2_space-MNI152NLin2009cAsym_desc-scale_bold.nii.gz        2    21748  rest  /data/MBDU/midla/notebooks/campcc/physio/new_cfds_rest/new_cfds_rest_subject_21748_session_2_run_1_task_rest.tsv
2    /data/MBDU/midla/data/derivatives/fitlins/rest_dm_only/sub-21748/ses-03/run-1/out/out/fitlins/sub-21748/ses-03/sub-21748_ses-03_task-rest_run-1_design.tsv  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/ses-03/func/sub-21748_ses-03_task-rest_run-1_echo-2_space-MNI152NLin2009cAsym_desc-preproc_bold.nii.gz  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/anat/sub-21748_space-MNI152NLin2009cAsym_label-GM_probseg.nii.gz    1  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-21748/out/fmriprep/sub-21748/ses-03/func/sub-21748_ses-03_task-rest_run-1_echo-2_space-MNI152NLin2009cAsym_desc-scale_bold.nii.gz        3    21748  rest  /data/MBDU/midla/notebooks/campcc/physio/new_cfds_rest/new_cfds_rest_subject_21748_session_3_run_1_task_rest.tsv
3    /data/MBDU/midla/data/derivatives/fitlins/rest_dm_only/sub-22293/ses-01/run-1/out/out/fitlins/sub-22293/ses-01/sub-22293_ses-01_task-rest_run-1_design.tsv  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-22293/out/fmriprep/sub-22293/ses-01/func/sub-22293_ses-01_task-rest_run-1_echo-2_space-MNI152NLin2009cAsym_desc-preproc_bold.nii.gz  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_rest/sub-22293/out/fmriprep/sub-22293/anat/sub-22293_space-MNI152NLin2009cAsym_label-GM_probseg.nii.gz    1  /data/MBDU/midla/data/derivatives/fmriprep/rn_aroma_20190910_2mm_re

In [219]:
rest_paths.to_csv('/data/MBDU/midla/notebooks/campcc/rest_paths_for_icc.csv')

In [196]:
dat_paths = pd.read_csv('/data/MBDU/midla/notebooks/campcc/dat_paths_12092019.csv')

included_subjects = pd.read_csv('/data/MBDU/midla/notebooks/campcc/test_retest/included_subjects.csv',index_col = 0)
dat_paths = dat_paths[dat_paths['subject'].isin(included_subjects['SDAN'])]
dat_paths = dat_paths.loc[dat_paths[dat_paths.columns[4:6]].duplicated(keep='last') == False]

single_ses_subs = dat_paths.loc[dat_paths.session.astype(int) <= 4, :].groupby('subject').session.nunique().reset_index().query('session <= 2').subject
dat_ind = ~dat_paths.subject.isin(single_ses_subs) & (dat_paths.session.astype(int) <= 4)
dat_paths = dat_paths.loc[dat_ind]

dat_paths.reset_index(inplace=True)
dat_paths = dat_paths.drop(columns=['index'])

cfds_physio = []
for _,row in dat_paths.iterrows():
    if (os.path.isfile('/data/MBDU/midla/data/bids/sub-{}/ses-0{}/func/sub-{}_ses-0{}_task-mid_run-{}_physio.tsv.gz'.format(row.subject,row.session,row.subject,row.session,row.run))):
        cfds_physio.append('/data/MBDU/midla/notebooks/campcc/physio/new_cfds_mid/new_cfds_mid_subject_{}_session_{}_run_{}_task_mid.tsv'.format(row.subject,row.session,row.run))
    else:
        cfds_physio.append('')
dat_paths['cfds_physio_path'] = cfds_physio


In [197]:
dat_paths.to_csv('/data/MBDU/midla/notebooks/campcc/dat_paths_for_icc.csv')